In [ ]:
#resources 
#https://towardsdatascience.com/building-an-image-color-analyzer-using-python-12de6b0acf74

In [1]:
from collections import Counter
from sklearn.cluster import KMeans
from matplotlib import colors
import matplotlib.pyplot as plt
import numpy as np
import cv2
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
import colorsys
import os
from fake_useragent import UserAgent

from time import sleep
import json

import contractions
import spacy
#from spacy.tokenizer import Tokenizer
import en_core_web_sm
import nltk
#from nltk.stem import WordNetLemmatizer
from nltk import bigrams, trigrams
from bs4 import BeautifulSoup, SoupStrainer
from urllib.request import Request, urlopen
import requests
import string
import regex as re
import collections
from lxml import etree
import csv 


In [2]:
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])
ua = UserAgent()
userAgent = ua.random
find_company_urls = False
write_company_csv = False

In [3]:
def rgb_to_hex(rgb_color):
    hex_color = "#"
    for i in rgb_color:
        i = int(i)
        hex_color += ("{:02x}".format(i))
    return hex_color

def prep_image(raw_img):
    modified_img = cv2.resize(raw_img, (900, 600), interpolation = cv2.INTER_AREA)
    modified_img = modified_img.reshape(modified_img.shape[0]*modified_img.shape[1], 3)
    return modified_img

def color_analysis(img, url, k=6):
    
    clf = KMeans(n_clusters = k)
    color_labels = clf.fit_predict(img)
    center_colors = clf.cluster_centers_    
    counts = Counter(color_labels)
    ordered_colors = [center_colors[i].round(3).tolist() for i in counts.keys()]
    hex_colors = [rgb_to_hex(ordered_colors[i]) for i in counts.keys()]    
    plt.figure(figsize = (12, 8))
    plt.pie(counts.values(), labels = hex_colors, colors = hex_colors)
    plt.title('color proportions from {u}'.format(u=url))
    plt.savefig('./plots/pie-' + url.replace('.', '-') + '.png')
    
    
    
    color_array = np.array(list(counts.values()))
    color_proportion = (color_array/sum(color_array)).round(3).tolist()
 
    
    color_dict = {}
    
    color_dict['centroids_rgb'] = ordered_colors
    color_dict['centroids_hex'] = hex_colors
    color_dict['color_counts'] = color_array.tolist()
    color_dict['color_proportion'] = color_proportion
    
    hsv = [list(colorsys.rgb_to_hsv(c[0], c[1], c[2])) for c in color_dict['centroids_rgb']]
    color_dict['centroids_hsv']=hsv
    
    #print(hex_colors)
    return color_dict 

In [4]:
def get_paragraph_text(url, hdr):
    
    try:
        
        req = Request(url,headers=hdr)
        page = urlopen(req)
    
    except:
        
        print("http failed, trying https:")
        
        try:
            url = url.replace('http:', 'https:')
            req = Request(url,headers=hdr)
            page = urlopen(req)
        
        except Exception as e:
            print("substitution of https also failed. Error is {}".format(e))
            
    else:
   
        soup = BeautifulSoup(page, 'html.parser')

        p=soup.find_all('p')
        text = ' '.join(t.get_text() for t in p)

        return text

class TextPreprocessor(object):
    def __init__(self):
        """
        TBD
        """

    def preprocess_df(self, df):
        return df.apply(self._preprocess_text)

    def preprocess_text(self, text):
        doc = nlp(text)
        removed_punct = self._remove_punct(doc)
        removed_stop_words = self._remove_stop_words(removed_punct)

        return self._lemmatize(removed_stop_words)

    def _remove_punct(self, doc):
        return [t for t in doc if t.text not in string.punctuation]

    def _remove_stop_words(self, doc):
        return [t for t in doc if not t.is_stop]

    def _lemmatize(self, doc):
        
        lemma_text = ' '.join([t.lemma_ for t in doc])
        
        return re.sub('\s+',' ',lemma_text)
        


In [ ]:
if find_company_urls:
    
    r = requests.get("https://www.bcorporation.net/sitemap/sitemap-0.xml")
    root = etree.fromstring(r.content)
    d='find-a-b-corp'
    hdr = {'User-Agent':str(ua.chrome)}

    urls=[]

    for sitemap in root:
        children = sitemap.getchildren()

        if 'find-a-b-corp/company/' in children[0].text:
            urls.append(children[0].text)

    company_urls=[]

    for idx, url in enumerate(urls):

        try:

            url_split=url.split('find-a-b-corp')

            redirect=url_split[0] + 'en-us/' + d + url_split[1]

            if '/en-us/en-us' not in redirect:

                company=redirect.split('/company/')[-1]



                req = Request(redirect,headers=hdr)
                page = urlopen(req)
                soup = BeautifulSoup(page, 'html.parser')


                #company_site=soup.text.split("Website")[1].split('www.')[1].split('.')[0]
                for ele in soup.text.split("Website")[1].split('www.'):

                    #find the first (non empty) part of the url after "www." since this will contain the beginning of the
                    #company's website
                    if len(ele) > 0:
                        company_site = ele.split('.')[0]
                        break



                company_url=soup.find('a', attrs={'href': re.compile(company_site)}).get('href')
                company_urls.append(company_url)
        except Exception as e:
            print(e, url)

    if write_company_csv:
        # opening the csv file in 'w+' mode
        file = open('b-corp-companies.csv', 'w+', newline ='')

        # writing the data into the file
        for element in company_urls:
            file.write(element + "\n")
        file.close()




In [ ]:
#company_urls = ['www.uber.com', 'www.lyft.com', 'www.doordash.com']
#company_urls = ['www.bsw.com']
#urls = ['www.lyft.com']
#check out https://github.com/robinreni96/Font_Recognition-DeepFont

In [15]:
with open('b-corp-companies.csv', newline='') as f:
    reader = csv.reader(f)
    company_urls = list(reader)

In [24]:
#company_urls= company_urls[653:]
#company_urls
len(company_urls)
company_urls= company_urls[49:]

In [20]:
def take_screenshot(url, driver):
    
    try:
        
        url = url.split('https://')[1]
        
        sleep(2)
        driver.get('https://' + url)
        #driver.get(url)
        sleep(2)


        S = lambda X: driver.execute_script('return document.body.parentNode.scroll'+X)
        driver.set_window_size(S('Width'),S('Height')) # May need manual adjustment

        el = driver.find_element(By.TAG_NAME, value='body')
        el.screenshot('./site-screenshots/'+ url.replace('.', '-') + '.png')
        
    except Exception as e:
        
        print("url {url} error {e}".format(url=url, e=e))
    

['https://psicometrix.cl']

In [25]:
overwrite_json=True
options = webdriver.ChromeOptions()
options.headless = True
options.add_argument(f'user-agent={userAgent}')
    
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
driver.maximize_window()
url_errors = {}
urls_color_dicts = []

if overwrite_json:
    #if the json already exists from a prior code run, delete it
    if os.path.exists('site_screenshot_colors.json'):
        os.remove('site_screenshot_colors.json')

for idx, url in enumerate(company_urls):
    
    
    print(url)
    
    try:
        
        url = url[0]
        
        take_screenshot(url)
        
#         url = url.split('https://')[1]
        
#         sleep(2)
#         driver.get('https://' + url)
#         #driver.get(url)
#         sleep(2)


#         S = lambda X: driver.execute_script('return document.body.parentNode.scroll'+X)
#         driver.set_window_size(S('Width'),S('Height')) # May need manual adjustment

#         el = driver.find_element(By.TAG_NAME, value='body')
#         el.screenshot('./site-screenshots/'+ url.replace('.', '-') + '.png')

        image = cv2.imread('./site-screenshots/'+ url.replace('.', '-') + '.png')
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        plt.imshow(image)

        modified_image = prep_image(image)
        color_dict = color_analysis(modified_image, url)
        color_dict['url'] = url
        color_dict['screenshot'] = url.replace('.', '-') + '.png'
        
        
        
        with open('site_screenshot_colors.json', 'a') as f:
            f.write(json.dumps(color_dict))
            f.write('\n')

                                      

        urls_color_dicts.append(color_dict)
        
        #font family is probably not reliable
        print(el.value_of_css_property("font-family"))
        print(el.value_of_css_property("background-color"))
        print(el.value_of_css_property("color"))
        print(el.value_of_css_property("font-family"))
        print(el.value_of_css_property("font-size"))
        
        
        
                
    
    except Exception as e:
        
        print("url {url} error {e}".format(url=url, e=e))
        
        url_errors[url] = e

#driver.quit()
#f.close()

print("end...")



====== WebDriver manager ======
Current google-chrome version is 101.0.4951
Get LATEST chromedriver version for 101.0.4951 google-chrome
Driver [/Users/amywinecoff/.wdm/drivers/chromedriver/mac64/101.0.4951.41/chromedriver] found in cache


['https://chroma.com']
Helvetica, Arial, sans-serif
rgba(0, 0, 0, 0)
rgba(34, 34, 34, 1)
Helvetica, Arial, sans-serif
14px
['https://Vitarock.com']
"Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif
rgba(255, 255, 255, 1)
rgba(51, 49, 50, 1)
"Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif
13px
['https://www.herbalist-alchemist.com']
"Fira Sans", "Trebuchet MS", Geneva, sans-serif
rgba(255, 255, 255, 1)
rgba(74, 74, 74, 1)
"Fira Sans", "Trebuchet MS", Geneva, sans-serif
15px
['https://www.beekeepersnaturals.com']
"Sofia Pro", system-ui, -apple-system, "system-ui", sans-serif
rgba(255, 255, 255, 1)
rgba(0, 0, 0, 1)
"Sofia Pro", system-ui, -apple-system, "system-ui", sans-serif
16px
['https://pharos.com']
freight-sans-pro, "Helvetica Neue", Helvetica, Helvetica, Arial, sans-serif
rgba(82, 81, 79, 1)
rgba(82, 81, 79, 1)
freight-sans-pro, "Helvetica Neue", Helvetica, Helvetica, Arial, sans-serif
16px
['https://www.dittohangers.com']
-apple-system, "system-ui", "Segoe UI

"Open Sans", Helvetica, sans-serif
rgba(255, 255, 255, 1)
rgba(64, 64, 64, 1)
"Open Sans", Helvetica, sans-serif
25.6px
['https://www.mas-business.com']
Oswald
rgba(255, 255, 255, 1)
rgba(0, 0, 0, 1)
Oswald
16px
['/en-us/movement/justice-equity-diversity-inclusion']
url /en-us/movement/justice-equity-diversity-inclusion error list index out of range
['https://www.r4sgroup.com']
url www.r4sgroup.com error Message: timeout: Timed out receiving message from renderer: 10.000
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f158 chromedriver + 393560
3   chromedriver                        0x000000010da4a0ec chromedriver + 307436
4   chromedriver                        0x000000010da48efa chromedriver + 302842
5   chromedriver                        0x000000010da493f

url www.vertandvogue.com error Message: timeout: Timed out receiving message from renderer: 10.000
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f158 chromedriver + 393560
3   chromedriver                        0x000000010da4a0ec chromedriver + 307436
4   chromedriver                        0x000000010da48efa chromedriver + 302842
5   chromedriver                        0x000000010da493fc chromedriver + 304124
6   chromedriver                        0x000000010da665de chromedriver + 423390
7   chromedriver                        0x000000010da9179c chromedriver + 599964
8   chromedriver                        0x000000010dab1482 chromedriver + 730242
9   chromedriver                        0x000000010da88b05 chromedriver + 563973
10  chromedriver             

url www.brandiq.biz error Message: timeout: Timed out receiving message from renderer: 10.000
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f158 chromedriver + 393560
3   chromedriver                        0x000000010da4a0ec chromedriver + 307436
4   chromedriver                        0x000000010da48efa chromedriver + 302842
5   chromedriver                        0x000000010da493fc chromedriver + 304124
6   chromedriver                        0x000000010da665de chromedriver + 423390
7   chromedriver                        0x000000010da9179c chromedriver + 599964
8   chromedriver                        0x000000010dab1482 chromedriver + 730242
9   chromedriver                        0x000000010da88b05 chromedriver + 563973
10  chromedriver                  

...

url www.tred.earth error Message: chrome not reachable
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f00f chromedriver + 393231
3   chromedriver                        0x000000010da4d0a2 chromedriver + 319650
4   chromedriver                        0x000000010da4da95 chromedriver + 322197
5   chromedriver                        0x000000010da4f822 chromedriver + 329762
6   chromedriver                        0x000000010da4830c chromedriver + 299788
7   chromedriver                        0x000000010da605b2 chromedriver + 398770
8   chromedriver                        0x000000010dac35fb chromedriver + 804347
9   chromedriver                        0x000000010dab1373 chromedriver + 729971
10  chromedriver                        0x000000010da87609 chromedriver +

url sourcegreenpackaging.com error Message: chrome not reachable
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f00f chromedriver + 393231
3   chromedriver                        0x000000010da4d0a2 chromedriver + 319650
4   chromedriver                        0x000000010da4da95 chromedriver + 322197
5   chromedriver                        0x000000010da4f822 chromedriver + 329762
6   chromedriver                        0x000000010da4830c chromedriver + 299788
7   chromedriver                        0x000000010da605b2 chromedriver + 398770
8   chromedriver                        0x000000010dac35fb chromedriver + 804347
9   chromedriver                        0x000000010dab1373 chromedriver + 729971
10  chromedriver                        0x000000010da87609 chro

url www.onesixthexpeditions.com error Message: chrome not reachable
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f00f chromedriver + 393231
3   chromedriver                        0x000000010da4d0a2 chromedriver + 319650
4   chromedriver                        0x000000010da4da95 chromedriver + 322197
5   chromedriver                        0x000000010da4f822 chromedriver + 329762
6   chromedriver                        0x000000010da4830c chromedriver + 299788
7   chromedriver                        0x000000010da605b2 chromedriver + 398770
8   chromedriver                        0x000000010dac35fb chromedriver + 804347
9   chromedriver                        0x000000010dab1373 chromedriver + 729971
10  chromedriver                        0x000000010da87609 c

url www.EcomHalo.com error Message: chrome not reachable
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f00f chromedriver + 393231
3   chromedriver                        0x000000010da4d0a2 chromedriver + 319650
4   chromedriver                        0x000000010da4da95 chromedriver + 322197
5   chromedriver                        0x000000010da4f822 chromedriver + 329762
6   chromedriver                        0x000000010da4830c chromedriver + 299788
7   chromedriver                        0x000000010da605b2 chromedriver + 398770
8   chromedriver                        0x000000010dac35fb chromedriver + 804347
9   chromedriver                        0x000000010dab1373 chromedriver + 729971
10  chromedriver                        0x000000010da87609 chromedriver

url www.believe-partners.com error Message: chrome not reachable
  (Session info: headless chrome=101.0.4951.64)
Stacktrace:
0   chromedriver                        0x000000010dee12c9 chromedriver + 5120713
1   chromedriver                        0x000000010de6fe33 chromedriver + 4656691
2   chromedriver                        0x000000010da5f00f chromedriver + 393231
3   chromedriver                        0x000000010da4d0a2 chromedriver + 319650
4   chromedriver                        0x000000010da4da95 chromedriver + 322197
5   chromedriver                        0x000000010da4f822 chromedriver + 329762
6   chromedriver                        0x000000010da4830c chromedriver + 299788
7   chromedriver                        0x000000010da605b2 chromedriver + 398770
8   chromedriver                        0x000000010dac35fb chromedriver + 804347
9   chromedriver                        0x000000010dab1373 chromedriver + 729971
10  chromedriver                        0x000000010da87609 chro

In [26]:
#len(url_errors.keys())
#idx
idx

3992

In [ ]:
full_url = "http://" + url
# hdr = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11',
#        'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
#        'Accept-Charset': 'ISO-8859-1,utf-8;q=0.7,*;q=0.3',
#        'Accept-Encoding': 'none',
#        'Accept-Language': 'en-US,en;q=0.8',
#        'Connection': 'keep-alive'}

hdr = {'User-Agent':str(ua.chrome)}

req = Request(full_url,headers=hdr)
page = urlopen(req)
soup = BeautifulSoup(page, 'html.parser')

main_site_text = get_paragraph_text(full_url, hdr).lower()
#print(main_site_text)

processed_text = TextPreprocessor().preprocess_text(main_site_text)
print(processed_text)

word_counts = collections.Counter(processed_text.split())
# bg = bigrams(ah_text.split())
# bigram_counts = collections.Counter(bg)
# tg = trigrams(ah_text.split())
# trigram_counts = collections.Counter(tg)

word_counts.most_common(50)
#bigram_counts.most_common(50)


In [ ]:
#element = driver.find_element(By.XPATH, "/html/body")
#element = driver.find_element(By.TAG_NAME, value='title')

# print(el.value_of_css_property("background-color"))
# print(el.value_of_css_property("color"))
# print(el.value_of_css_property("font-family"))
# print(el.value_of_css_property("font-size"))

In [ ]:
#are the rgb values, cluster centroids, cluster centroid proportions, or hsv values predictive of the type of business

In [ ]:
# #Save this part
# r = requests.get("https://www.bcorporation.net/sitemap/sitemap-0.xml")
# root = etree.fromstring(r.content)
# d='find-a-b-corp'
# hdr = {'User-Agent':str(ua.chrome)}

# urls=[]

# company_urls=[]
# for sitemap in root:
#     children = sitemap.getchildren()
#     #xmlDict[children[0].text] = children[1].text
#     if 'find-a-b-corp/company/' in children[0].text:
#         urls.append(children[0].text)

# for idx, url in enumerate(urls):

#     url_split=url.split('find-a-b-corp')

#     redirect=url_split[0] + 'en-us/' + d + url_split[1]

#     company=redirect.split('/company/')[-1]



#     req = Request(redirect,headers=hdr)
#     page = urlopen(req)
#     soup = BeautifulSoup(page, 'html.parser')

#     company_url=soup.find('a', attrs={'href': re.compile(company)}).get('href')
#     company_urls.append(company_url)


In [ ]:
company_urls[0]

In [ ]:
# # websplit=soup.text.split("Website")
# # print(websplit[1].split('www.')[1].split('.')[0])
# #websplit=soup.text.split("Website")[1].split('www.')[1].split('.')[0]
# #print(websplit)
# #soup.text.split("Website")[1].split('www.')[1].split('.')[0]
# redirect="https://www.bcorporation.net/en-us/find-a-b-corp/company/redemption-rock-brewing-co"
# req = Request(redirect,headers=hdr)
# page = urlopen(req)
# soup = BeautifulSoup(page, 'html.parser')
# for ele in soup.text.split("Website")[1].split('www.'):
#     if len(ele) > 0:
#         company_site = ele.split('.')[0]
#         break


# #[1].split('www.')
# #[0].split('.')[0]